In [1]:
using Gync, Vega

In [ ]:
floating_mean(v::Vector, window) = 
    map(i->mean(v[i:i+window]), 1:length(v)-window)

floating_acceptance(c::Mamba.AbstractChains, window) = 
    floating_acceptance(c.value[:,1,1]|>vec, window)

floating_acceptance(v::Vector, window) = 
    floating_mean(map(!=, v[1:end-1], v[2:end]), window)

floating_distance(v::Vector, window) = 
    floating_mean(abs(map(-, v[1:end-1], v[2:end])), window)

In [251]:
iters = 20_000
rho = 0.5
sigmay0 = 3
sigmap  = 2

config = ModelConfig(Subject(:lausanne, 1), rho, sigmay0, sigmap)

sim = runsim(config, iters, relprop=0.1);

MCMC Simulation of 20000 Iterations x 1 Chain...

Chain 1:   0% [0:14:50 of 0:14:50 remaining]
Chain 1:  10% [0:13:50 of 0:15:22 remaining]
Chain 1:  20% [0:12:31 of 0:15:39 remaining]
Chain 1:  30% [0:11:04 of 0:15:48 remaining]
Chain 1:  40% [0:09:35 of 0:15:59 remaining]
Chain 1:  50% [0:08:00 of 0:16:01 remaining]
Chain 1:  60% [0:06:24 of 0:16:00 remaining]
Chain 1:  70% [0:04:49 of 0:16:05 remaining]
Chain 1:  80% [0:03:14 of 0:16:09 remaining]
Chain 1:  90% [0:01:38 of 0:16:20 remaining]
Chain 1: 100% [0:00:00 of 0:16:27 remaining]



In [252]:
window = 500

f = floating_acceptance(sim.value[:,8,1]|>vec,window)
lineplot(x=1:length(f), y=f) |> display

f = floating_distance(sim.value[:,8,1]|>vec,window)
lineplot(x=1:length(f), y=f) |> display

## Debug the adaptive rank

tune=sim.model.samplers[1].tune
p = tune.m / (tune.m + 1.0)
Sigma = (tune.scale^2 / 115 / p) * (tune.Mvv - tune.Mv * tune.Mv')
F = cholfact(Sigma, :U, Val{true})
println("rank Sigma: $(rank(Sigma)) rank Chol: $(rank(F))")
sim

rank Sigma: 115 rank Chol: 115


Object of type "Mamba.ModelChains"

Iterations = 1:20000
Thinning interval = 1
Chains = 1
Samples per chain = 20000

20000x116x1 Array{Float64,3}:
[:, :, 1] =
 7309.9   7309.9   192.2    2.371    …  3.3169e-5   2.9879e-5   -137.443 
 7309.9   7309.9   192.2    2.371       3.3169e-5   2.9879e-5   -137.443 
 7309.9   7309.9   192.2    2.371       3.3169e-5   2.9879e-5   -137.443 
 7380.97  7093.39  195.182  2.25418     3.13897e-5  3.18646e-5  -134.041 
 7380.97  7093.39  195.182  2.25418     3.13897e-5  3.18646e-5  -134.041 
 7380.97  7093.39  195.182  2.25418  …  3.13897e-5  3.18646e-5  -134.041 
 7380.97  7093.39  195.182  2.25418     3.13897e-5  3.18646e-5  -134.041 
 7380.97  7093.39  195.182  2.25418     3.13897e-5  3.18646e-5  -134.041 
 7380.97  7093.39  195.182  2.25418     3.13897e-5  3.18646e-5  -134.041 
 7380.97  7093.39  195.182  2.25418     3.13897e-5  3.18646e-5  -134.041 
 7380.97  7093.39  195.182  2.25418  …  3.13897e-5  3.18646e-5  -134.041 
 7380.97  7093.39  195.182 

In [263]:
tune.SigmaLm

115x115 Array{Float64,2}:
 -0.0145252    -0.0193683    -0.0060947    …  0.0         0.0  0.0  0.0  0.0
 -0.033379     -0.0190368    -0.0136235       0.0         0.0  0.0  0.0  0.0
  0.0078236     0.00625124    0.0181918       0.0         0.0  0.0  0.0  0.0
  0.00772746   -0.0447089     0.0152905       0.0         0.0  0.0  0.0  0.0
 -0.000404588  -0.00417335    0.025939        0.0         0.0  0.0  0.0  0.0
  0.019476      0.0458485    -0.021955     …  0.0         0.0  0.0  0.0  0.0
  0.0139663     0.0206391     0.00780743      0.0         0.0  0.0  0.0  0.0
  0.00279073    0.0191223     0.0171293       0.0         0.0  0.0  0.0  0.0
  0.031389      0.0285546    -0.0207959       0.0         0.0  0.0  0.0  0.0
 -0.00459854    0.00395575   -0.00928556      0.0         0.0  0.0  0.0  0.0
  0.0486814    -0.00694111   -0.0174365    …  0.0         0.0  0.0  0.0  0.0
  0.00942492    0.0369064     0.00212148      0.0         0.0  0.0  0.0  0.0
 -0.0237343     0.007978     -0.00772813      0.0 

In [182]:
import Vega: VegaData

# Construct VegaData from a given Markov Chain
VegaData(chains::Mamba.AbstractChains, args...) = VegaData(squeeze(chains.value, 3), chains.names, name="samples")

function VegaData{S<:AbstractString}(m::Matrix, colnames::Vector{S}; 
    name::AbstractString = string("table_",lowercase(randstring(5))))
    
    n = size(m, 1)
    d = [Dict() for i in 1:n]
    for i in 1:n
        for (col, colname) in enumerate(colnames)
            colname = replace(replace(colname,"[",""),"]","")
            d[i][colname] = m[i,col]
        end
    end        
    VegaData(name = name, values = d)
end

Vega.VegaData

In [265]:
function scales(param::AbstractString) 
    xscale = VegaScale(name="x", _type = "linear", range="width", zero=true,
        domain=VegaDataRef(data="samples", field="bin_$param"))
    yscale = VegaScale(name="y", range="height",
        domain=VegaDataRef(data=param, field="count"))
    [xscale, yscale]
end

parammarks(param) =
    VegaMark(_type="rect", 
        from=VegaMarkFrom(data=param), 
        properties=VegaMarkProperties(
            update=VegaMarkPropertySet(
                x=    VegaValueRef(scale = "x", field = "bin_$param"),
                width=VegaValueRef(value = 3),
                y=    VegaValueRef(scale = "y", field = "count"),
                y2=   VegaValueRef(scale = "y", value=0),
                fill= VegaValueRef(value = "#bbb"))))


paramgroup(param::AbstractString) = 
    VegaMark(_type="group",
        name="group_$param",
        scales=scales(param),
        axes = [VegaAxis(_type="x", scale="x")],
        marks=[parammarks(param)], 
        properties=VegaMarkProperties(
            update=VegaMarkPropertySet(
                x =      VegaValueRef(value = 0),
                y =      VegaValueRef(value = 0),
                width =  VegaValueRef(value = 400),
                height = VegaValueRef(value = 200))))


# transformation 
bin_transform(param) =
    VegaTransform(Dict(
        "type" => "bin",
        "maxbins" => 100,
        "field" => param, 
        "output" => Dict(
            "start" => "bin_$param")))

countdata(param) = 
    VegaData(
        name=param, 
        source="samples", 
        transform=[count_transform("bin_$param")])

count_transform(groupby) = 
    VegaTransform(Dict(
        "type" => "aggregate",
        "groupby" => [groupby],
        "summarize" => Dict("*"=> ["count"])))

function parfilter(param, allparms) 
    res = VegaTransform[]
    for p in allparms
        (param == p) && continue
        push!(res, VegaTransform(Dict(
            "type" => "filter",
            "test" => "(min_$p == max_$p || (datum.$p >= min_$p && datum.$p <= max_$p))")))
    end
    res
end

scopesignal = Dict{Any,Any}("name"=>"scope", "init"=>Dict("width"=>0),
    "streams"=>Dict("type"=>"mousedown", "expr"=>"eventGroup()"))

function signals(param)
    startsig = Dict(
        "name" => "start_$param",
        "init" => -1,
        "streams" => Dict("type"=>"@group_$param:mousedown",
            "expr"=>"eventX(scope)",
            "scale"=>Dict("scope"=>"scope","name"=>"x", "invert"=>true)))

    endsig = Dict(
        "name" => "end_$param",
        "init" => -1,
        "streams" => Dict("type"=>"@group_$param:mousedown, [@group_$param:mousedown, window:mouseup] > window:mousemove",
            "expr"=>"clamp(eventX(scope), 0, scope.width)",
            "scale"=>Dict("scope"=>"scope","name"=>"x", "invert"=>true)))

    minsig = Dict("name"=>"min_$param", "expr"=>"max(min(start_$param, end_$param), 0)")
    maxsig = Dict("name"=>"max_$param", "expr"=>"min(max(start_$param, end_$param), 10000000)")
    
    Dict{Any,Any}[startsig, endsig, minsig, maxsig]
end





function plotit(sim)
    data = VegaData(sim)

    v = VegaVisualization()
    v.data = [data]
    
    data.transform = VegaTransform[]
    v.marks = VegaMark[]
    v.signals = [scopesignal]

    allparms = keys(data.values[1])

    for (i,param) in enumerate(allparms)
        
        group = paramgroup(param)
        group.properties.update.y.value = (i-1) * 250
        
        counts = countdata(param)
        unshift!(counts.transform, parfilter(param, allparms)...)
        
        push!(data.transform, bin_transform(param))
        push!(v.data,         counts)
        push!(v.marks,        group)
        push!(v.signals,      signals(param)...)
    end
    v
end

v = plotit(sim[:, [8,5,7], 1])

In [266]:
using Vega
import KernelDensity.kde

function plot_species(c::Mamba.AbstractChains, kde=false)
    @assert size(c,[2,3]) == (1,1)
    
    data = c.value|>vec
    
    v = kde ? plot_kde(data) : histogram(x=data, nbins = 40)
    
    title!(v, title=c.names[1])
end

function plot_kde(data::Vector)
    npoints = 2^14
    bw = maximum(data) / npoints * 5
    k  = kde(data, npoints=npoints, bandwidth=bw)
    
    v=lineplot(x=k.x,y=k.density)
    v.scales[1].zero=false
    v
end

function slices(a,dim)
    inds = Any[(:) for i in 1:length(size(a))]
    map(1:size(a,dim)) do i
        inds[dim] = i
        getindex(a,inds...)
    end
end

function plot(c::Mamba.AbstractChains)
    reduce(layer,map(plot_species,slices(c,2)))
end

@time v = plot_species(sim[:,8,1])

5.924917 seconds (2.35 M allocations: 95.377 MB, 13.34% gc time)
